In [1]:
import os
import pandas as pd
import numpy as np
import json
import traceback

date = '2019-12-20_21'
root_dir = '/Users/Leo/Documents/github/GradProj/'
example_label_file = root_dir + 'DataSet/result/' + date + '/stream_tag.txt'
example_label_df = pd.read_table(example_label_file, sep='\s+', header=None)
example_label_df[3] = 443
example_label_df[4].value_counts()
example_label = {tuple(example_label_df.iloc[i,0:4].values):example_label_df.iloc[i,4] for i in example_label_df.index}
#example_label



In [3]:
log_dir = root_dir + 'DataSet/DataTag/log/' + date

log_files = [
    log_dir + '/http.log.2019-12-20',
    log_dir + '/http.log.2019-12-21',
    log_dir + '/http2.log.2019-12-20',
    log_dir + '/http2.log.2019-12-21'
]

tuple2log = dict()

for log_file in log_files:
    with open(log_file, errors='ignore') as f:
        lines = f.readlines()
        for line in lines:
            stream_tuple = line.split(',')[3].split()
            #print(stream_tuple)
            try:
                stream_tuple1 = (stream_tuple[0], int(stream_tuple[1]), stream_tuple[2], int(stream_tuple[3]))
                tuple2log[stream_tuple1] = line
            except:
                print(line)
                #traceback.print_exc()

#for key in tuple2log.keys():
 #   print(key)

Fri Dec 20 14:57:57 2019, FATAL, __on_response_prepare_context, Standlone HTTP response emerged. Malformed HTTP Protocol, detached. 

Fri Dec 20 15:04:34 2019, FATAL, __on_response_prepare_context, Standlone HTTP response emerged. Malformed HTTP Protocol, detached. 

Fri Dec 20 15:17:06 2019, FATAL, __on_response_prepare_context, Standlone HTTP response emerged. Malformed HTTP Protocol, detached. 

Fri Dec 20 15:17:48 2019, FATAL, __on_response_prepare_context, Standlone HTTP response emerged. Malformed HTTP Protocol, detached. 

Fri Dec 20 15:17:52 2019, FATAL, __on_response_prepare_context, Standlone HTTP response emerged. Malformed HTTP Protocol, detached. 

Fri Dec 20 15:17:57 2019, FATAL, __on_response_prepare_context, Standlone HTTP response emerged. Malformed HTTP Protocol, detached. 

Fri Dec 20 15:45:53 2019, FATAL, http_connection_entry, 192.168.50.150 64330 47.93.77.222 443: Failed at parsing stream as HTTP, 26, HPE_UNEXPECTED_CONTENT_LENGTH, unexpected content-length header

In [29]:
ssl_parse_stat_json_file = root_dir + 'DataSet/result/' + date + '/ssl_parse_stat.txt'

log_miss_dip_set = set()
log_hit_dip_set = set()


with open(ssl_parse_stat_json_file) as f:
    lines = f.readlines()
    tag_miss = 0
    tag_miss_log_miss = 0
    tag_miss_log_hit = 0
    tag_hit = 0
    tag_hit_log_miss = 0
    for line in lines:
        line = json.loads(line)
        flow_key = (line['sip'], line['sport'], line['dip'], line['dport'])
        if flow_key not in example_label:
            tag_miss += 1
            if flow_key not in tuple2log.keys():
                #print(flow_key)
                dip = flow_key[2]
                log_miss_dip_set.add(dip)
                tag_miss_log_miss += 1
            else:
                #print(tuple2log[flow_key])
                tag_miss_log_hit += 1
        else:
            tag_hit += 1
            dip = flow_key[2]
            log_hit_dip_set.add(dip)
            if flow_key not in tuple2log.keys():
                tag_hit_log_miss += 1
    
    print('tag_miss: ' + str(tag_miss))
    print('tag_miss_log_miss: ' + str(tag_miss_log_miss))
    print('tag_miss_log_hit: ' + str(tag_miss_log_hit))
    print('tag_hit: ' + str(tag_hit))
    print('tag_hit_log_miss: ' + str(tag_hit_log_miss))
    
    len1 = len(log_hit_dip_set)
    len2 = len(log_miss_dip_set)
    print(len1)
    print(len2)
    
    union_set = log_hit_dip_set.intersection(log_miss_dip_set)
    
    print(len(union_set))
    
    for dip in log_miss_dip_set:
        print(dip)
    
    #print('log_hit_dip_set: ' + str(len(log_hit_dip_set)))
    #print('log_miss_dip_set: '+ str(len(log_miss_dip_set))
          
    #print(log_hit_dip_set.intersection(log_miss_dip_set))

tag_miss: 11149
tag_miss_log_miss: 10293
tag_miss_log_hit: 856
tag_hit: 9253
tag_hit_log_miss: 0
403
836
175
110.249.203.158
17.57.145.68
17.188.147.169
17.188.158.45
17.188.128.21
216.58.200.234
23.23.181.12
17.248.160.79
139.215.192.211
125.39.21.5
23.21.243.53
23.23.211.244
17.248.161.135
54.243.231.118
54.243.137.15
124.132.134.230
122.14.43.168
54.225.146.80
182.254.50.64
104.71.49.33
50.17.244.107
203.119.207.252
50.19.224.184
122.14.43.39
54.243.85.14
54.243.172.191
17.188.153.169
17.188.142.166
17.188.128.144
54.243.85.164
54.225.169.64
203.187.160.136
23.23.198.201
17.142.171.6
203.187.160.135
17.188.142.37
17.248.161.144
23.23.145.83
17.248.159.177
107.22.243.29
54.235.187.18
17.188.158.49
54.243.167.92
17.248.161.39
17.248.158.140
54.235.129.20
17.188.166.214
27.221.24.226
54.243.174.139
54.243.64.240
61.240.28.1
17.248.161.44
203.208.50.34
17.188.131.147
54.225.86.247
17.248.158.108
69.192.8.189
184.73.246.3
50.16.198.205
17.252.156.210
203.208.43.101
182.254.59.158
103.135

In [40]:
dict1 = dict()
dict1[(1,2,3)] = 3
dict1[(3,2,1)] = 1

key1 = (1,2,3)
if key1 not in dict1.keys():
    print("miss")
else:
    print("hit")

hit
